In [1]:
import numpy as np
import pandas as pd
from lightgbm import LGBMClassifier
from sklearn.metrics import roc_auc_score
from sklearn.model_selection import train_test_split, cross_validate, StratifiedGroupKFold, KFold
from catboost import CatBoostClassifier


In [2]:
train_df = pd.read_parquet("train_data.pqt")
train_df.__len__

<bound method DataFrame.__len__ of             id     date  balance_amt_avg  balance_amt_max  balance_amt_min  \
0            0  month_1         0.744845         0.705492         1.287207   
1            0  month_2         1.049605         0.831916         2.458609   
2            0  month_3         0.692653         0.740253         0.430042   
3            1  month_1        -0.081586        -0.091860        -0.114040   
4            1  month_2        -0.094962        -0.100504        -0.119302   
...        ...      ...              ...              ...              ...   
599995  199998  month_2        -0.156775        -0.204960        -0.125987   
599996  199998  month_3        -0.156776        -0.204960        -0.125995   
599997  199999  month_1        -0.156712        -0.204913        -0.125831   
599998  199999  month_2        -0.156712        -0.204913        -0.125831   
599999  199999  month_3        -0.156712        -0.204913        -0.125831   

        balance_amt_day_avg 

In [3]:
train_df.head(12)

id     date  balance_amt_avg  balance_amt_max  balance_amt_min  \
0    0  month_1         0.744845         0.705492         1.287207   
1    0  month_2         1.049605         0.831916         2.458609   
2    0  month_3         0.692653         0.740253         0.430042   
3    1  month_1        -0.081586        -0.091860        -0.114040   
4    1  month_2        -0.094962        -0.100504        -0.119302   
5    1  month_3        -0.090605        -0.114275        -0.114119   
6    2  month_1        -0.154685        -0.186795        -0.122805   
7    2  month_2        -0.152784        -0.193686        -0.122805   
8    2  month_3        -0.148737        -0.187003        -0.112416   
9    3  month_1        -0.156643        -0.204861        -0.125660   
10   3  month_2        -0.156666        -0.204790        -0.125995   
11   3  month_3        -0.156522        -0.204718        -0.125759   

    balance_amt_day_avg     channel_code      city      city_type  \
0              0.748101   channel_code_5   city_23    city_type_0   
1              1.053805   channel_code_5   city_23    city_type_0   
2              0.695747   channel_code_5   city_23    city_type_0   
3             -0.080890   channel_code_2   city_14    city_type_0   
4             -0.094307   channel_code_2   city_14    city_type_0   
5             -0.089937   channel_code_2   city_14    city_type_0   
6             -0.154215  channel_code_12  city_613  city_type_306   
7             -0.152308  channel_code_12  city_613  city_type_306   
8             -0.148249  channel_code_12  city_613  city_type_306   
9             -0.156179  channel_code_14   city_21    city_type_0   
10            -0.156202  channel_code_14   city_21    city_type_0   
11            -0.156058  channel_code_14   city_21    city_type_0   

       index_city_code  ...  cnt_cred_g_oper_3m  cnt_days_cred_g_oper_3m  \
0   index_city_code_39  ...            0.951166                 0.568681   
1   index_city_code_39  ...            0.948812                 0.499716   
2   index_city_code_39  ...            0.946458                 0.442244   
3                 None  ...            0.945281                 0.407762   
4                 None  ...            0.946066                 0.430750   
5                 None  ...            0.948027                 0.488221   
6                 None  ...            0.944497                 0.384773   
7                 None  ...            0.944497                 0.384773   
8                 None  ...            0.944497                 0.384773   
9   index_city_code_46  ...            0.944497                 0.384773   
10  index_city_code_46  ...            0.944497                 0.384773   
11  index_city_code_46  ...            0.944497                 0.384773   

   sum_deb_h_oper_3m cnt_deb_h_oper_3m  cnt_days_deb_h_oper_3m  \
0           0.897565          0.553624                0.774354   
1           0.785029          0.551904                0.696576   
2           0.877050          0.551044                0.663243   
3           0.369318          0.567093                0.785465   
4           0.067275          0.559928                0.696576   
5           0.043221          0.560788                0.707687   
6          -0.165588          0.546889                0.407687   
7          -0.165588          0.546889                0.407687   
8          -0.165588          0.546889                0.407687   
9          -0.165588          0.546889                0.407687   
10         -0.165588          0.546889                0.407687   
11         -0.165588          0.546889                0.407687   

    sum_cred_h_oper_3m  cnt_cred_h_oper_3m  cnt_days_cred_h_oper_3m  \
0             0.936506            0.295984                 0.967947   
1             0.990157            0.298873                 0.945969   
2             0.810065            0.294829                 0.956958   
3            -0.184002            0.253523                 0.46

In [272]:
cat_cols = [
    "channel_code", "city", "city_type",
    "okved", "segment", "start_cluster",
    "index_city_code", "ogrn_month", "ogrn_year",
]

In [273]:

train_df[cat_cols] = train_df[cat_cols].astype("category")

In [274]:
train_df = train_df.drop(["id", "date"], axis=1)


In [278]:
cluster_weights = pd.read_excel("cluster_weights.xlsx").set_index("cluster")
weights_dict = cluster_weights["unnorm_weight"].to_dict()
cat_features = [col for col in test_df_missing.columns if test_df_missing[col].dtype.name == 'category' or test_df_missing[col].dtype.name == 'object']
for col in cat_features:
   test_df_missing[col] = test_df_missing[col].astype('category')

cat_features = [col for col in test_df_missing.columns if test_df_missing[col].dtype.name == 'category' or test_df_missing[col].dtype.name == 'object']
for col in cat_features:
    test_df_missing[col] = test_df_missing[col].cat.add_categories('Missing').fillna('Missing')

cat_features

['channel_code',
 'city',
 'city_type',
 'index_city_code',
 'ogrn_month',
 'ogrn_year',
 'okved',
 'segment']

In [279]:
models = [CatBoostClassifier().load_model(f'model_14d_611i_8split\model_{i}.cbm') for i in range(8)]
#models = [CatBoostClassifier().load_model(f'model_{i}.cbm') for i in range(8)]
predictions = np.array([model.predict(test_df_missing) for model in models])

predictions_transposed = predictions.T


In [280]:
predictions_transposed

array([[['{α}', '{α}', '{α}', ..., '{α}', '{α}', '{α}'],
        ['{α}', '{α}', '{α}', ..., '{α}', '{α}', '{α}'],
        ['{other}', '{other}', '{other}', ..., '{other}', '{other}',
         '{other}'],
        ...,
        ['{α}', '{α}', '{α}', ..., '{α}', '{α}', '{α}'],
        ['{α}', '{α}', '{α}', ..., '{α}', '{α}', '{α}'],
        ['{α}', '{α}', '{α, γ}', ..., '{α}', '{α}', '{α}']]], dtype=object)

In [281]:
import numpy as np

consensus_predictions = []
# print(predictions_transposed)
for row in predictions_transposed[0]:
    print(row)
    vals, counts = np.unique(row, return_counts=True)
    print(vals)
    print(counts)
    index = np.argmax(counts)
    consensus_predictions.append(vals[index])


consensus_predictions = np.array(consensus_predictions)



['{α}' '{α}' '{α}' '{α}' '{α}' '{α}' '{α}' '{α}']
['{α}']
[8]
['{α}' '{α}' '{α}' '{α}' '{α}' '{α}' '{α}' '{α}']
['{α}']
[8]
['{other}' '{other}' '{other}' '{other}' '{other}' '{other}' '{other}'
 '{other}']
['{other}']
[8]
['{α}' '{α}' '{α}' '{α}' '{α}' '{α}' '{α}' '{α}']
['{α}']
[8]
['{α}' '{α}' '{α}' '{α}' '{α}' '{α}' '{α}' '{α}']
['{α}']
[8]
['{α, δ}' '{α, δ}' '{α}' '{other}' '{α}' '{α, δ}' '{α}' '{other}']
['{other}' '{α, δ}' '{α}']
[2 3 3]
['{α}' '{α}' '{α}' '{α}' '{α}' '{α}' '{α}' '{α}']
['{α}']
[8]
['{α}' '{α}' '{α}' '{α}' '{α}' '{α}' '{α}' '{α}']
['{α}']
[8]
['{α}' '{α}' '{α}' '{α}' '{α}' '{α}' '{α}' '{α}']
['{α}']
[8]
['{α}' '{α}' '{α}' '{α}' '{α}' '{α}' '{α}' '{α}']
['{α}']
[8]
['{α, μ}' '{α}' '{α}' '{α, η}' '{α}' '{α}' '{α}' '{α, η}']
['{α, η}' '{α, μ}' '{α}']
[2 1 5]
['{α}' '{α}' '{α}' '{α}' '{α}' '{α}' '{α}' '{α}']
['{α}']
[8]
['{α}' '{α}' '{α}' '{α}' '{α}' '{α}' '{}' '{α}']
['{}' '{α}']
[1 7]
['{α}' '{α}' '{α}' '{α}' '{α}' '{α}' '{α}' '{α}']
['{α}']
[8]
['{α}' '{α, η}' '{

IOPub data rate exceeded.
The Jupyter server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--ServerApp.iopub_data_rate_limit`.

Current values:
ServerApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
ServerApp.rate_limit_window=3.0 (secs)



In [282]:
consensus_predictions

array(['{α}', '{α}', '{other}', ..., '{α}', '{α}', '{α}'], dtype='<U9')

In [283]:

# Теперь можно безопасно заполнять пропуски в 'start_cluster'
for i, idx in enumerate(missing_indices):
    test_df.at[idx, 'start_cluster'] = consensus_predictions[i]




In [284]:
test_df.head(30)

balance_amt_avg  balance_amt_max  balance_amt_min  balance_amt_day_avg  \
0         -0.096224         0.335496        -0.125995            -0.095578   
1         -0.024255        -0.059806        -0.124295            -0.023381   
2          0.045988         0.049418        -0.125995             0.047079   
3         -0.156722        -0.204920        -0.125856            -0.156258   
4         -0.156722        -0.204920        -0.125856            -0.156258   
5         -0.156722        -0.204920        -0.125856            -0.156258   
6         -0.096506         0.185905        -0.125995            -0.095856   
7          0.572242         1.502779        -0.125995             0.574963   
8         -0.048015         0.448252        -0.125995            -0.047215   
9         -0.156623        -0.204813        -0.125665            -0.156159   
10        -0.156579        -0.204813        -0.125501            -0.156115   
11        -0.156579        -0.204813        -0.125501            -0.156115   
12              NaN              NaN              NaN                  NaN   
13        -0.153379        -0.201932        -0.125995            -0.154155   
14        -0.113771         0.098011        -0.125995            -0.113174   
15        -0.096582         0.079861        -0.125995            -0.095932   
16         0.543302         0.712921        -0.125995             0.545933   
17        -0.154554        -0.203773        -0.124405            -0.154084   
18        -0.154522        -0.203773        -0.124405            -0.154052   
19        -0.154442        -0.203773        -0.124206            -0.153972   
20        -0.125748        -0.180259        -0.064704            -0.125188   
21        -0.117949        -0.136387        -0.056818            -0.117366   
22        -0.123198        -0.177398        -0.056818            -0.122630   
23              NaN              NaN              NaN                  NaN   
24        -0.156516        -0.204687        -0.125866            -0.156262   
25              NaN              NaN              NaN                  NaN   
26        -0.156552        -0.204687        -0.125995            -0.156216   
27        -0.155099        -0.202485        -0.125995            -0.154630   
28        -0.146092        -0.184405        -0.125961            -0.145596   
29        -0.148696        -0.186584        -0.125922            -0.148207   

       channel_code       city       city_type     index_city_code  \
0   channel_code_12    city_14     city_type_0                 NaN   
1   channel_code_12    city_14     city_type_0                 NaN   
2   channel_code_12    city_14     city_type_0                 NaN   
3    channel_code_9    city_76     city_type_0                 NaN   
4    channel_code_9    city_76     city_type_0                 NaN   
5    channel_code_9    city_76     city_type_0                 NaN   
6   channel_code_12    city_14     city_type_0  index_city_code_78   
7   channel_code_12    city_14     city_type_0  index_city_code_78   
8   channel_code_12    city_14     city_type_0  index_city_code_78   
9    channel_code_7    city_31     city_type_0                 NaN   
10   channel_code_7    city_31     city_type_0                 NaN   
11   channel_code_7    city_31     city_type_0                 NaN   
12              NaN        NaN             NaN                 NaN   
13   channel_code_7        NaN             NaN                 NaN   
14   channel_code_8        NaN             NaN   index_city_code_2   
15   channel_code_8        NaN             NaN   index_city_code_2   
16   channel_code_8        NaN             NaN   index_city_code_2   
17  channel_code_12    city_53  city_type_7557  index_city_code_82   
18  channel_code_12    city_53  city_type_7557  index_city_code_82   
19  channel_code_12    city_53  city_type_7557  index_city_code_82   
20   channel_code_5    city_14     city_type_0  index_city_code_72   
21   channel_code_5    city_14     city_type_

In [285]:

# test_df.to_csv('test_df_filled.csv', index=False)


In [286]:
test_df.__len__()

290120

In [287]:
# Загрузка оригинального датафрейма
original_test_df = pd.read_parquet("test_data.pqt")

# Обновление столбца 'start_cluster' в оригинальном датафрейме значениями из обработанного test_df
original_test_df['start_cluster'] = test_df['start_cluster']

# Сохранение обновлённого датафрейма в CSV
original_test_df.to_csv('test_df_filled_night_timur.csv', index=False)

